In [ ]:
import random
import gc
import sys
import numpy as np
import torch
import torch.nn as nn
import torch.nn.functional as F
import matplotlib.pyplot as plt
from numpy import linalg as la
from tqdm.notebook import tqdm
from sklearn.model_selection import train_test_split
%matplotlib inline

sys.path.insert(0, '../../../methods')
from dnn_ahmed2023 import *
from music import *

In [ ]:
# random seed
seed = 1234
random.seed(seed)
np.random.seed(seed)
torch.manual_seed(seed)

In [ ]:
# load data
data = np.load('../../../data/experiment_2/scenario_1//data_train.npy', allow_pickle=True)

In [ ]:
def get_coarray(X, sensor_pos, M):
    X_out = np.zeros((len(X), 2*M-1), dtype=complex)
    X_mask = np.ones((len(X), 2*M-1))

    for n in range(len(X)):
        print(f"{n}/{len(X)}")
        counter = np.zeros(2*M-1)
        for i in range(sensor_pos[n].shape[0]):
            for j in range(sensor_pos[n].shape[0]):
                idx = int(M+2*(sensor_pos[n][i]-sensor_pos[n][j])-1)
                #if sensor_pos[n][j] > sensor_pos[n][i]:
                X_out[n,idx] = X_out[n,idx] + X[n][i,j]
                #else:
                #    X_out[n,idx] = X_out[n,idx] + X[n][j,i]

                X_mask[n,idx] = 0
                counter[idx] += 1

        for i in range(len(counter)):
            if counter[i] > 0:
                X_out[n,i] = X_out[n,i] / counter[i]

    return X_out, X_mask

In [ ]:
def spatial_smoothing(X):
    X = X.reshape(-1,1)
    num_subarrays = int((X.shape[0]-1)/2)
    subarray_length = num_subarrays+1

    smoothed_cov = np.zeros((subarray_length, subarray_length), dtype=complex)
    for i in range(num_subarrays+1):
        smoothed_cov = smoothed_cov + X[i:i+subarray_length] @ X[i:i+subarray_length].conj().T

    smoothed_cov = smoothed_cov / (num_subarrays+1)

    return smoothed_cov

In [ ]:
# get labels and data seperately
truths = [s['label'] for s in data]
cm = [s['cm'] for s in data]
cm_intact = [s['cm_intact_true'] for s in data]
sensor_pos = [s['sensor_pos'][:,0] for s in data]

sensor_pos_intact = []
for i in range(len(sensor_pos)):
    sensor_pos_intact.append(np.array([1,2,3,4,5,6,11,16])*0.5)

M = 16
coarray_intact, _ = get_coarray(cm_intact, sensor_pos_intact, M)

cm_intact_ss = np.zeros((coarray_intact.shape[0],M,M),dtype=complex)
for i in range(coarray_intact.shape[0]):
    print("SS", i)
    cm_intact_ss[i,:,:] = spatial_smoothing(coarray_intact[i,:])

for i in range(len(cm)):
    print("Intact", i)
    intact_pos = np.array([1,2,3,4,5,6,11,16])-1
    pos = (sensor_pos[i]*2-1).astype(int)
    cm_with_missings = np.zeros((8,8), dtype=complex)
    for j in range(len(intact_pos)):
        for k in range(len(intact_pos)):
            if np.sum(pos==intact_pos[j])==0 or np.sum(pos==intact_pos[k])==0:
                cm_with_missings[j,k] = 0
            else:
                cm_with_missings[j,k] = cm[i][np.where(pos==intact_pos[j])[0], np.where(pos==intact_pos[k])[0]]

    cm[i] = cm_with_missings

#truths = np.stack(truths).squeeze(2)
cm = np.stack(cm)
cm = cm.reshape(cm.shape[0],-1, order='F')
cm_intact_ss = cm_intact_ss.reshape(cm_intact_ss.shape[0],-1, order='F')
#cm_true = np.stack(cm_true)

np.save(f"../../../data/experiment_2/scenario_1/cm.npy", cm)
np.save(f"../../../data/experiment_2/scenario_1/cm_ss.npy", cm_intact_ss)

In [ ]:
del data
gc.collect()

In [ ]:
# select channels
X = [np.real(cm), np.imag(cm)]
X = np.hstack(X)
y = [np.real(cm_intact_ss), np.imag(cm_intact_ss)]
y = np.hstack(y)

# standardize
# for i in range(data.shape[2]):
#     for j in range(data.shape[3]):
#         for k in range(data.shape[1]):
#             data[:,k,i,j] -= np.mean(data[:,k,i,j])
#             data[:,k,i,j] /= np.std(data[:,k,i,j])
#
# # nan to zero for diagonals
# data = np.nan_to_num(data)

In [ ]:
del cm
del cm_intact_ss
gc.collect()

In [ ]:
# train, val split
val_ratio = 0.1
X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=val_ratio, random_state=seed)

In [ ]:
print(np.min(X_train))

In [ ]:
print(np.max(X_train))

In [ ]:
# min-max scaling
X_val = (X_val-np.min(X_train)) / (np.max(X_train)-np.min(X_train))
X_train = (X_train-np.min(X_train)) / (np.max(X_train)-np.min(X_train))

In [ ]:
# dataloader
class FastTensorDataLoader:
    """
    A DataLoader-like object for a set of tensors that can be much faster than
    TensorDataset + DataLoader because dataloader grabs individual indices of
    the dataset and calls cat (slow).
    Source: https://discuss.pytorch.org/t/dataloader-much-slower-than-manual-batching/27014/6
    """
    def __init__(self, *tensors, batch_size=32, shuffle=False):
        """
        Initialize a FastTensorDataLoader.
        :param *tensors: tensors to store. Must have the same length @ dim 0.
        :param batch_size: batch size to load.
        :param shuffle: if True, shuffle the data *in-place* whenever an
            iterator is created out of this object.
        :returns: A FastTensorDataLoader.
        """
        assert all(t.shape[0] == tensors[0].shape[0] for t in tensors)
        self.tensors = tensors

        self.dataset_len = self.tensors[0].shape[0]
        self.batch_size = batch_size
        self.shuffle = shuffle

        # Calculate # batches
        n_batches, remainder = divmod(self.dataset_len, self.batch_size)
        if remainder > 0:
            n_batches += 1
        self.n_batches = n_batches
    def __iter__(self):
        if self.shuffle:
            r = torch.randperm(self.dataset_len)
            self.tensors = [t[r] for t in self.tensors]
        self.i = 0
        return self

    def __next__(self):
        if self.i >= self.dataset_len:
            raise StopIteration
        batch = tuple(t[self.i:self.i+self.batch_size] for t in self.tensors)
        self.i += self.batch_size
        return batch

    def __len__(self):
        return self.n_batches

In [ ]:
# dataloader, model, criterion and optimizer initialization
batch_size = 512
learning_rate = 1e-3
device = 'cuda' if torch.cuda.is_available() else 'cpu'
print(device)

train_loader = FastTensorDataLoader(X_train, y_train, batch_size=batch_size, shuffle=True)
val_loader = FastTensorDataLoader(X_val, y_val, batch_size=batch_size)
model2 = Network().to(device)
criterion = nn.MSELoss()
optimizer = torch.optim.Adam(params=model2.parameters(), lr=learning_rate)

In [ ]:
del X_train
del X_val
del y_train
del y_val
gc.collect()

In [ ]:
# training
num_epochs = 356
best_loss = 1000
lr_decay_patience = 10
lr_decay_counter = 0
train_loss_list = np.zeros(num_epochs)
train_rmse_list = np.zeros(num_epochs)
train_acc_list = np.zeros(num_epochs)
val_loss_list = np.zeros(num_epochs)
val_rmse_list = np.zeros(num_epochs)
val_acc_list = np.zeros(num_epochs)
# train_loss_list = np.load('/content/drive/MyDrive/Research/Experiments/train_loss.npy')
# train_rmse_list = np.load('/content/drive/MyDrive/Research/Experiments/train_rmse.npy')
# train_acc_list = np.load('/content/drive/MyDrive/Research/Experiments/train_acc.npy')
# val_loss_list = np.load('/content/drive/MyDrive/Research/Experiments/val_loss.npy')
# val_rmse_list = np.load('/content/drive/MyDrive/Research/Experiments/val_rmse.npy')
# val_acc_list = np.load('/content/drive/MyDrive/Research/Experiments/val_acc.npy')

for epoch in range(0,num_epochs):
    model2.train()
    running_loss = 0
    counter = 0

    for batch_id, (X, y) in tqdm(enumerate(train_loader), leave=False, desc="training"):
        X = torch.tensor(X).float().to(device)
        y = torch.tensor(y).float().to(device)

        prob = model2(X)
        loss = criterion(prob,y)

        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        running_loss += loss.detach().data * y.shape[0]
        counter += y.shape[0]

        del X
        del y
        del loss
        del prob
    gc.collect()


    train_loss = running_loss/counter
    train_loss_list[epoch] = train_loss

    torch.cuda.empty_cache()

    # validation
    with torch.no_grad():
        model2.eval()
        running_loss = 0
        counter = 0

        for batch_id, (X, y) in tqdm(enumerate(val_loader), leave=False, desc="validation"):
            X = torch.tensor(X).float().to(device)
            y = torch.tensor(y).float().to(device)

            prob = model2(X)
            loss = criterion(prob,y)

            running_loss += loss.detach().data * y.shape[0]
            counter += y.shape[0]

            del X
            del y
            del loss
            del prob
        gc.collect()

        val_loss = running_loss/counter
        val_loss_list[epoch] = val_loss

    print(f"epoch {epoch+1}, train-loss {train_loss:.4f}, val-loss {val_loss:.4f}")

    if val_loss < best_loss:
        best_loss = val_loss
        lr_decay_counter = 0
        torch.save(model2.state_dict(), '../../../results/experiment_2/scenario_1/dnn_ahmed2023.pt')
        print(f"model is saved")
    else:
        lr_decay_counter += 1

    if lr_decay_counter == lr_decay_patience:
        lr_decay_counter = 0
        learning_rate *= 0.7
        learning_rate = max([learning_rate, 1e-7])
        print(f"learning rate decayed to {learning_rate:.4f}")

        for g in optimizer.param_groups:
            g['lr'] = learning_rate

    np.save('../../../results/experiment_2/scenario_1/train_loss.npy', train_loss_list)
    np.save('../../../results/experiment_2/scenario_1/train_rmse.npy', train_rmse_list)
    np.save('../../../results/experiment_2/scenario_1/train_acc.npy', train_acc_list)
    np.save('../../../results/experiment_2/scenario_1/val_loss.npy', val_loss_list)
    np.save('../../../results/experiment_2/scenario_1/val_rmse.npy', val_rmse_list)
    np.save('../../../results/experiment_2/scenario_1/val_acc.npy', val_acc_list)


In [ ]:
# loss curves
plt.figure(figsize=(10,5))
plt.plot(range(len(train_loss_list))[:356], train_loss_list[:356])
plt.plot(range(len(val_loss_list))[:356], val_loss_list[:356])
plt.title("training and validation loss curves")
plt.xlabel("epoch")
plt.ylabel("cross entropy loss")
plt.legend(["train", "val"])
plt.grid()

In [ ]:
def get_cov(X, num_sensors):
    X = np.reshape(X.cpu(), (-1,2), order='F')
    cov = np.zeros(X.shape[0], dtype=complex)
    cov = np.vectorize(complex)(X[:,0].cpu().numpy(), X[:,1].cpu().numpy())
    cov = np.reshape(cov, (num_sensors,num_sensors), order='F')

    return cov

In [ ]:
max_train = 279.0601042529362

In [ ]:
min_train = -59.24640924326781

In [ ]:
snr_list = [-20,-15,-10,-5,0,5,10,15,20,25,30]
T_list = [100,200,500,1000,2000,5000,10000]
rmse_list1 = []
rmse_list2 = []

for snr in snr_list:
    # load data
    data = np.load(f'../../../data/experiment_2/scenario_1/data_test_snr{snr}_t1000.npy', allow_pickle=True)

    # get labels and data seperately
    cm = [s['cm'] for s in data]
    truths = [s['label'] for s in data]
    sensor_pos = [s['sensor_pos'][:,0] for s in data]

    for i in range(len(cm)):
        intact_pos = np.array([1,2,3,4,5,6,11,16])-1
        pos = (sensor_pos[i]*2-1).astype(int)
        cm_intact = np.zeros((8,8), dtype=complex)
        for j in range(len(intact_pos)):
            for k in range(len(intact_pos)):
                if np.sum(pos==intact_pos[j])==0 or np.sum(pos==intact_pos[k])==0:
                    cm_intact[j,k] = 0
                else:
                    cm_intact[j,k] = cm[i][np.where(pos==intact_pos[j])[0], np.where(pos==intact_pos[k])[0]]

        cm[i] = cm_intact

    cm = np.stack(cm)
    cm = cm.reshape(cm.shape[0],-1, order='F')
    sensor_pos = np.stack(sensor_pos)

    # convert truths to matrix by padding
    truths_matrix = np.zeros((len(truths), 4))
    num_sources = np.zeros(len(truths))
    for i in range(len(truths)):
        truths_matrix[i,0:truths[i].shape[0]] = truths[i].reshape(-1,)
        num_sources[i] = truths[i].shape[0]
    truths = truths_matrix

    # select channels
    X = [np.real(cm), np.imag(cm)]
    X = np.hstack(X)

    # min-max scaling
    X = (X-min_train) / (max_train-min_train)
    # # standardize
    # for i in range(data.shape[2]):
    #     for j in range(data.shape[3]):
    #         for k in range(data.shape[1]):
    #             data[:,k,i,j] -= np.mean(data[:,k,i,j])
    #             data[:,k,i,j] /= np.std(data[:,k,i,j])
    #
    # # nan to zero for diagonals
    # data = np.nan_to_num(data)

    # dataloader, model, criterion and optimizer initialization
    batch_size = 1
    device = 'cuda' if torch.cuda.is_available() else 'cpu'

    test_loader = FastTensorDataLoader(X, truths, sensor_pos, num_sources, batch_size=batch_size)
    model2 = Network().to(device)
    model2.load_state_dict(torch.load('../../../results/experiment_2/scenario_1/dnn_ahmed2023.pt', map_location=torch.device('cpu')))
    criterion = nn.MSELoss()

    # testing
    with torch.no_grad():
        model2.eval()
        running_loss = 0
        counter = 0
        p_list = []
        y_list = []
        t_list = []

        for batch_id, (X, t, pos, n) in enumerate(test_loader):
            X = torch.tensor(X).float().to(device)
            t = torch.tensor(t).float().to(device)
            pos = pos.squeeze(0)
            n = int(n.squeeze(0))

            X_reconstructed = model2(X)
            X_reconstructed = get_cov(X_reconstructed, 16)

            pos_reconstructed = np.zeros((16,3))
            pos_reconstructed[:,0] = np.arange(16)*0.5

            p, spectrum = music(X_reconstructed, X_reconstructed.shape[0], n, pos_reconstructed, 1)

            if snr==10 and batch_id==0:
                np.save(f'../../../results/experiment_2/scenario_1/dnn_ahmed2023_spectrum_{t.cpu()}deg.npy', spectrum)

            t, _ = torch.sort(t[0,:n])
            p, _ = torch.sort(torch.tensor(p))

            p_list.append(p.cpu())
            t_list.append(t.cpu())

            del X
            del p
        gc.collect()

        p_list = np.concatenate(p_list,axis=0)
        t_list = np.concatenate(t_list,axis=0)
        test_rmse = np.sqrt(np.mean((t_list-p_list)**2))
        rmse_list1.append(test_rmse.item())

        gc.collect()

    print(f"snr {snr}dB, T {1000}, test-rmse {test_rmse:.4f}")

    np.save(f'../../../results/experiment_2/scenario_1/dnn_ahmed2023_preds_snr{snr}_t1000.npy', p_list)
    np.save(f'../../../results/experiment_2/scenario_1/dnn_ahmed2023_truths_snr{snr}_t1000.npy', t_list)

for T in T_list:
    # load data
    data = np.load(f'../../../data/experiment_2/scenario_1/data_test_snr-10_t{T}.npy', allow_pickle=True)

    # get labels and data seperately
    cm = [s['cm'] for s in data]
    truths = [s['label'] for s in data]
    sensor_pos = [s['sensor_pos'][:,0] for s in data]

    for i in range(len(cm)):
        intact_pos = np.array([1,2,3,4,5,6,11,16])-1
        pos = (sensor_pos[i]*2-1).astype(int)
        cm_intact = np.zeros((8,8), dtype=complex)
        for j in range(len(intact_pos)):
            for k in range(len(intact_pos)):
                if np.sum(pos==intact_pos[j])==0 or np.sum(pos==intact_pos[k])==0:
                    cm_intact[j,k] = 0
                else:
                    cm_intact[j,k] = cm[i][np.where(pos==intact_pos[j])[0], np.where(pos==intact_pos[k])[0]]

        cm[i] = cm_intact

    cm = np.stack(cm)
    cm = cm.reshape(cm.shape[0],-1, order='F')
    sensor_pos = np.stack(sensor_pos)

    # convert truths to matrix by padding
    truths_matrix = np.zeros((len(truths), 4))
    num_sources = np.zeros(len(truths))
    for i in range(len(truths)):
        truths_matrix[i,0:truths[i].shape[0]] = truths[i].reshape(-1,)
        num_sources[i] = truths[i].shape[0]
    truths = truths_matrix

    # select channels
    X = [np.real(cm), np.imag(cm)]
    X = np.hstack(X)

    # min-max scaling
    X = (X-min_train) / (max_train-min_train)
    # # standardize
    # for i in range(data.shape[2]):
    #     for j in range(data.shape[3]):
    #         for k in range(data.shape[1]):
    #             data[:,k,i,j] -= np.mean(data[:,k,i,j])
    #             data[:,k,i,j] /= np.std(data[:,k,i,j])
    #
    # # nan to zero for diagonals
    # data = np.nan_to_num(data)

    # dataloader, model, criterion and optimizer initialization
    batch_size = 1
    device = 'cuda' if torch.cuda.is_available() else 'cpu'

    test_loader = FastTensorDataLoader(X, truths, sensor_pos, num_sources, batch_size=batch_size)
    model2 = Network().to(device)
    model2.load_state_dict(torch.load('../../../results/experiment_2/scenario_1/dnn_ahmed2023.pt', map_location=torch.device('cpu')))
    criterion = nn.MSELoss()

    # testing
    with torch.no_grad():
        model2.eval()
        running_loss = 0
        counter = 0
        p_list = []
        y_list = []
        t_list = []

        for batch_id, (X, t, pos, n) in enumerate(test_loader):
            X = torch.tensor(X).float().to(device)
            t = torch.tensor(t).float().to(device)
            pos = pos.squeeze(0)
            n = int(n.squeeze(0))

            X_reconstructed = model2(X)
            X_reconstructed = get_cov(X_reconstructed, 16)
            pos_reconstructed = np.zeros((16,3))
            pos_reconstructed[:,0] = np.arange(16)*0.5

            p, spectrum = music(X_reconstructed, X_reconstructed.shape[0], n, pos_reconstructed, 1)

            t, _ = torch.sort(t[0,:n])
            p, _ = torch.sort(torch.tensor(p))

            p_list.append(p.cpu())
            t_list.append(t.cpu())

            del X
            del p
        gc.collect()

        p_list = np.concatenate(p_list,axis=0)
        t_list = np.concatenate(t_list,axis=0)
        test_rmse = np.sqrt(np.mean((t_list-p_list)**2))
        rmse_list2.append(test_rmse.item())

        gc.collect()

    print(f"snr -10 dB, T {T}, test-rmse {test_rmse:.4f}")

    np.save(f'../../../results/experiment_2/scenario_1/dnn_ahmed2023_preds_snr-10_t{T}.npy', p_list)
    np.save(f'../../../results/experiment_2/scenario_1/dnn_ahmed2023_truths_snr-10_t{T}.npy', t_list)

np.save('../../../results/experiment_2/scenario_1/dnn_ahmed2023_rmse1.npy', rmse_list1)
np.save('../../../results/experiment_2/scenario_1/dnn_ahmed2023_rmse2.npy', rmse_list2)

In [ ]:
# plot rmse values
plt.figure()
plt.plot(snr_list, rmse_list1, '-o')
plt.title("rmse values for different snr levels")
plt.xlabel("snr (dB)")
plt.ylabel("rmse (deg)")
plt.legend(['DNN + MUSIC Ahmed 2023'])
plt.yscale("log")
plt.grid()

plt.figure()
plt.plot(T_list, rmse_list2, '-o')
plt.title("rmse values for different snapshot numbers")
plt.xlabel("T")
plt.ylabel("rmse (deg)")
plt.legend(['DNN + MUSIC Ahmed 2023'])
plt.yscale("log")
plt.grid()